# Hyperspectral Band Selection

In this notebook, we'll demonstrate how to use our Inter-band redundancy method (IBRA) and the [Greedy Spectral Selection](https://www.mdpi.com/2072-4292/13/18/3649) (GSS) for hyperspectral band selection. IBRA can also be used in combination with Principal Component Analysis (PCA) and Partial Least Squares (PLS) for dimensionality reduction.




## Load your data

You can bring your own HSI classification dataset. Format the input data as a set of image data cubes of shape $(N, w, h, b)$, where $N$ is the number of data cubes, $w$ and $h$ are the width and the height of the cubes, and $b$ is the number of spectral bands. You could use the `createImageCubes` method, provided [here](https://github.com/NISL-MSU/HSI-BandSelection/blob/master/src/HSIBandSelection/readSAT.py#L47), as a reference to format your data.

In this example, we will load the Indian Pines dataset, which is an image with shape `(145, 145, 200)`.

In [1]:
import os
import os.path as osp
import numpy as np
import cv2
from torchvision import transforms
import torch
from skimage import io
from PIL import Image

In [2]:
folder_dir = osp.join('Aerial Data', 'Collection') #path to full files

image_hsi_rad = io.imread(osp.join(folder_dir, 'image_hsi_radiance.tif'))
image_hsi_rad = np.transpose(image_hsi_rad, [1,2,0])[53:,7:,:]
image_hsi_rad = np.clip(image_hsi_rad, 0, 2**14)/2**14

print(image_hsi_rad.shape)

(1920, 3968, 51)


In [3]:
get_labels=np.asarray(
                [
                        [255, 0, 0],
                        [0, 255, 0],
                        [0, 0, 255],
                        [0, 255, 255],
                        [255, 127, 80],
                        [153, 0, 0],
                        ]
                )

def encode_segmap( mask):
        mask = mask.astype(int)
        label_mask = np.zeros((mask.shape[0], mask.shape[1]), dtype=np.int16)
        for ii, label in enumerate(get_labels):
            label_mask[np.where(np.all(mask == label, axis=-1))[:2]] = ii
        label_mask = label_mask.astype(int)
        return label_mask

In [4]:
labels = io.imread(osp.join(folder_dir, 'image_labels.tif'))[53:,7:,:]
labels = encode_segmap(labels)

In [5]:
patch_size = 5
H, W, C = image_hsi_rad.shape

# 패치 개수
num_patches_h = H // patch_size
num_patches_w = W // patch_size

patch_data = []
patch_labels = []

for i in range(num_patches_h):
    for j in range(num_patches_w):
        data_patch = image_hsi_rad[i*patch_size:(i+1)*patch_size, j*patch_size:(j+1)*patch_size, :]
        labels_patch = labels[i*patch_size:(i+1)*patch_size, j*patch_size:(j+1)*patch_size]
        patch_data.append(data_patch)
        patch_labels.append(labels_patch)

# 리스트를 numpy 배열로 변환
patch_data = np.stack(patch_data)  # Shape: (N, 64, 64, 51)
patch_labels = np.stack(patch_labels)  # Shape: (N, 64, 64, 51)
patch_labels = patch_labels[:,patch_size // 2,patch_size // 2]
print(patch_data.shape) 
print(patch_labels.shape) 

(304512, 5, 5, 51)
(304512,)


In [6]:
patch_data=patch_data[0::30,:,:,:] # Only use ~10,000 samples
patch_labels=patch_labels[0::30]

print(patch_data.shape) 
print(patch_labels.shape) 

(10151, 5, 5, 51)
(10151,)


In [7]:
from torch.utils.data import Dataset

class HyperspectralDatasetWrapper(Dataset):
    def __init__(self, data, labels):
        self.data = data
        self.labels = labels
        # train_x, train_y, ind 속성 정의
        self.train_x = data
        self.train_y = labels.astype(np.float32)
        self.ind = [i for i in range(self.train_x.shape[-1])]
        self.name = 'AeroRIT'

    def __len__(self):
        return len(self.data)

    def __getitem__(self, idx):
        return self.data[idx], self.labels[idx]

dataset = HyperspectralDatasetWrapper(patch_data, patch_labels)


In [8]:
from HSIBandSelection.SelectBands import SelectBands
GPU_NUM = 0 # GPU number
device = torch.device(f'cuda:{GPU_NUM}' if torch.cuda.is_available() else 'cpu')
selector = SelectBands(dataset=dataset, method='GSS', nbands=5,device=device) # Methods: IBRA, GSS, PCA, PLS

From the SelectBands class, we call the `run_selection` method. **Parameters**:

*   `init_vf`: Initial Variance Inflation Factor threshold (used for IBRA). *Default: 12*
*   `final_vf`: Final Variance Inflation Factor threshold (used for IBRA). *Default: 5*



**Return**:

If the selected method is IBRA:

*   `VIF_best`: The VIF threshold at which the best results were obtained
*   `IBRA_best`: The best pre-selected bands using Iner-band redundancy
*   `stats_best`: The best performance metric values obtained after 5x2 CV using the selected bands

If the selected method is GSS:

*   `VIF_best`: The VIF threshold at which the best results were obtained
*   `IBRA_best`: The best pre-selected bands using Iner-band redundancy
*   `GSS_best`: The best combination of bands obtained using GSS
*   `stats_best`: The best performance metric values obtained after 5x2 CV using the selected bands

If the selected method is PCA or PLS:

*   `VIF_best`: The VIF threshold at which the best results were obtained
*   `IBRA_best`: The best pre-selected bands using Iner-band redundancy
*   `reduced_dataset`: The reduced dataset after applying PCA or PLS to the pre-selected bands
*   `stats_best`: The best performance metric values obtained after 5x2 CV using the reduced bands

**IMPORTANT**: This code is implemented using Pytorch. If you're running this on Google Colab, change the runtime type to GPU to accelerate the training process!

In [9]:
VIF_best, IBRA_best, GSS_best, stats_best =selector.run_selection(init_vf=12, final_vf=5)

*************************************
Testing VIF threshold: 12
*************************************
Selecting bands:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50]
Executing IBRA + GSS (Greddy Spectral Selection)
	Analyzing candidate combination 1. 5x2 CV using bands: [35, 37, 38, 39, 40]


  0%|          | 0/10 [00:00<?, ?it/s]/home/bkang/DPS/Hyperspectral/HSIBandSelection/Classification/CNNStrategy.py:150: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  self.mo

	Mean F1: 0.6943649862427753
			Multicolinearity analysis. Variance Inflation Factor of band 35 is 246.5
			Multicolinearity analysis. Variance Inflation Factor of band 37 is 578.72
			Multicolinearity analysis. Variance Inflation Factor of band 38 is 454.96
			Multicolinearity analysis. Variance Inflation Factor of band 39 is 459.21
			Multicolinearity analysis. Variance Inflation Factor of band 40 is 347.49
	Analyzing candidate combination 2. 5x2 CV using bands: [35, 38, 39, 40, 46]


  0%|          | 0/10 [00:00<?, ?it/s]/home/bkang/DPS/Hyperspectral/HSIBandSelection/Classification/CNNStrategy.py:150: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  self.mo

	Mean F1: 0.7218639823599307
	Best selection so far: [35, 38, 39, 40, 46]with an F1 score of 0.7218639823599307
			Multicolinearity analysis. Variance Inflation Factor of band 35 is 220.54
			Multicolinearity analysis. Variance Inflation Factor of band 38 is 413.74
			Multicolinearity analysis. Variance Inflation Factor of band 39 is 466.36
			Multicolinearity analysis. Variance Inflation Factor of band 40 is 411.11
			Multicolinearity analysis. Variance Inflation Factor of band 46 is 148.39
	Analyzing candidate combination 3. 5x2 CV using bands: [35, 38, 40, 45, 46]


...

	Mean F1: 0.81860682332817
	Best selection so far: [13, 27, 30, 34, 50]with an F1 score of 0.8298627641820048
			Multicolinearity analysis. Variance Inflation Factor of band 1 is 52.44
			Multicolinearity analysis. Variance Inflation Factor of band 2 is 62.24
			Multicolinearity analysis. Variance Inflation Factor of band 29 is 12.52
			Multicolinearity analysis. Variance Inflation Factor of band 34 is 42.81
			Multicolinearity analysis. Variance Inflation Factor of band 50 is 36.96
	Analyzing candidate combination 47. 5x2 CV using bands: [0, 1, 29, 34, 50]


  0%|          | 0/10 [00:00<?, ?it/s]/home/bkang/DPS/Hyperspectral/HSIBandSelection/Classification/CNNStrategy.py:150: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  self.mo

	Mean F1: 0.8026445079292136
	Best selection so far: [13, 27, 30, 34, 50]with an F1 score of 0.8298627641820048
Selecting bands:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50]

 Training a model using 5x2 CV using the final selected or reduced bands...


/home/bkang/DPS/Hyperspectral/HSIBandSelection/Classification/CNNStrategy.py:150: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  self.model.network.load_state_dict(torch.load

Mean F1 score: 85.19549241569332

The best F1 performance was achieved using a VIF = 12
The best band combination obtained using GSS was [13, 27, 30, 34, 50]


In [10]:
print('The best metrics were obtained using a VIF value of {}'.format(VIF_best))
print('The pre-selected bands obtained by IBRA wew {}'.format(IBRA_best))
print('The pre-selected bands obtained by IBRA+GSS wew {}'.format(GSS_best))
print('The best classification metrics were as follows:')
print(stats_best)

The best metrics were obtained using a VIF value of 12
The pre-selected bands obtained by IBRA wew [17, 31, 41]
The pre-selected bands obtained by IBRA+GSS wew [13, 27, 30, 34, 50]
The best classification metrics were as follows:
Stats(mean_accuracy=92.58865248226951, std_accuracy=0.33511790661883284, mean_precision=88.397661335862, std_precision=1.2676867785377905, mean_recall=83.39084824478923, std_recall=1.7503787170176366, mean_f1=85.19549241569332, std_f1=1.2895387773580724)
